In [12]:
import logging
import os
import socket
import sys
import time

import numpy as np
import pickle as pk
import tenseal as ts

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix, f1_score, recall_score, precision_score, accuracy_score
                           
os.chdir("/home/apignet/homomorphic-encryption/ckks_titanic/")
from src.features import build_features
from models import encrypted_LR
from models import unencrypted_LR

In [2]:
%load_ext memory_profiler

In [3]:
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
1

1

# definition of parameters

### Paths

In [4]:
WORKING_DIR = os.getcwd()

LOG_PATH = WORKING_DIR+"/reports/log/"
LOG_FILENAME = "Alice"

### Paths

In [5]:
fileHandler = logging.FileHandler("{0}/{1}.log".format(LOG_PATH, LOG_FILENAME))
streamHandler = logging.StreamHandler(sys.stdout)
logging.basicConfig(format="%(asctime)s  [%(levelname)-8.8s]  %(message)s", 
                    datefmt='%m/%d/%Y %I:%M:%S %p', 
                    level = logging.INFO, 
                    handlers=[fileHandler, streamHandler]
                   )

### Training variables

In [6]:
EPOCH = 40
LEARNING_RATE = 0.9
MOMENTUM_RATE = 0.6
REGULARIZATION_RATE = 0.5
VERBOSE = 4
SAVE_WEIGHT = 4
N_JOBS = 8

### Socket Variables

In [7]:
HOST = '127.0.0.1'  # The server's hostname or IP address
PORT = 65432        # The port used by the server
PACKETS_SIZE = 16
SENTINEL = b'BREAK'

# Esthablishing the communication with Bob


In [8]:
try:
    BOB = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
    BOB.connect((HOST, PORT))
    logging.info(str(BOB.recv(1024)))
except:
    logging.info("Alice is not listening, binding a server...")
    s = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
    s.bind((HOST, PORT))
    s.listen()
    BOB, BOB_ADDR = s.accept()
    logging.info('Connected by '+ str(BOB_ADDR))
    BOB.send(b'Connection accepted')


08/05/2020 03:32:02 PM  [INFO    ]  Connected by('127.0.0.1', 55086)


## Receiving the public context

In [9]:
logging.info('Waiting for serialized context')
b_data = b''.join(iter((lambda :BOB.recv(PACKETS_SIZE)), SENTINEL))
logging.info('Context received. Strating deserialization.')
context = ts.context_from(b_data)
logging.info('Context successfully deserialized')

08/05/2020 03:32:52 PM  [INFO    ]  Waiting for serialized context
08/05/2020 03:33:23 PM  [INFO    ]  Context received. Strating deserialization.
08/05/2020 03:33:26 PM  [INFO    ]  Context successfully deserialized


## Receiving serialized data

In [13]:
b_data = b''.join(iter((lambda :BOB.recv(PACKETS_SIZE)), SENTINEL))
len_X = pk.loads(b_data)
b_Y = [None for _ in range(len_X)]
b_X = [None for _ in range(len_X)]

In [23]:
while True:
    b_data = b''.join(iter((lambda :BOB.recv(PACKETS_SIZE)), SENTINEL))
    if b_data==b'DONE': break
    data = pk.loads(b_data)
    print(data[0])
    b_X[data[0]]=data[1]
    b_Y[data[0]]=data[2]
    data = b'NEXT'
    for n in range(len(data) // PACKETS_SIZE + 1):
        BOB.send(data[n * PACKETS_SIZE: (n + 1) * PACKETS_SIZE])
    BOB.send(SENTINEL)
    
data = b'OKDONE'
    for n in range(len(data) // PACKETS_SIZE + 1):
        BOB.send(data[n * PACKETS_SIZE: (n + 1) * PACKETS_SIZE])
    BOB.send(SENTINEL)

0
1
6
9
18
19
27
30
32
35
41
61
68
70
86
94
98
108
110
113
116
117
118
122
124
125
130
131
132
149
151
158
161
166
169
176
178
185
198
200
207
215
228
244
249
251
258
261
267
268
287
288
301
304
305
312
314
321
324
338
340
350
353
357
360
362
364
375
381
390
392
397
401
405
429
441
452
455
459
470
473
480
489
496
499
506
507
508
515
524
525
529
539
540


In [24]:
 missing_id = [idx for idx,e in enumerate(b_X) if e is None]
missing_id

[2,
 3,
 7,
 8,
 11,
 12,
 13,
 14,
 15,
 16,
 20,
 22,
 24,
 25,
 26,
 28,
 33,
 34,
 36,
 37,
 38,
 39,
 40,
 43,
 44,
 45,
 46,
 51,
 52,
 53,
 55,
 56,
 57,
 58,
 59,
 60,
 62,
 64,
 65,
 71,
 72,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 87,
 88,
 90,
 92,
 93,
 95,
 96,
 97,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 107,
 111,
 114,
 115,
 120,
 121,
 123,
 126,
 127,
 128,
 133,
 134,
 135,
 136,
 137,
 139,
 140,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 150,
 152,
 153,
 154,
 155,
 156,
 157,
 159,
 162,
 163,
 164,
 167,
 168,
 171,
 172,
 173,
 174,
 175,
 177,
 179,
 180,
 181,
 182,
 183,
 184,
 186,
 187,
 188,
 190,
 192,
 193,
 194,
 195,
 196,
 199,
 201,
 202,
 203,
 204,
 206,
 208,
 209,
 210,
 211,
 212,
 214,
 217,
 218,
 219,
 220,
 221,
 222,
 223,
 224,
 225,
 227,
 229,
 230,
 231,
 232,
 233,
 234,
 236,
 238,
 239,
 240,
 241,
 242,
 245,
 246,
 247,
 248,
 250,
 253,
 255,
 256,
 257,
 259,
 260,
 262,
 263,
 264,
 265,
 266,
 269,
 270,
 271,
 2

In [25]:
b_X[4]

b'\x08 \x12\xf9\x8ae^\xa1\x10\x03\x05\x01\x00\x00yE\x19\x00\x00\x00\x00\x00x\x9cLweXU\r\xb4\xf4\xe9\xdag\xefCw\x83\xa4\xa4H\x8b\x88J\xb7\xb4 (\x1d\x82\xa0\x82\x02\xd2 \x8a\xb4(\xa0\x12\xd2\x08RJ\x87 \xdd\x1d\xd2! -%\xcd\xf7>\xdf\xbd?\xee\xfcX3\xcf\xfa?k\xd6\x04\x06\xc0\xb3>g\x04F\x0f\xf3\xe9\xba\xb4\xdc\xb8r\xad@\xa4\xc8e\xf4Dn\xf1j\x8d3\xfa\xa4\xd8-\x01\x8e\x80\xfd/\x14\xfe\x87p\xb0\xff\x8bG\x8a\xf7\xd2\xc8\x90\xe8\xff\x14\x1d\x8c\xed\x7fw\xa8\xff?/\xdfn)\xb1/\x10AK~A\x8bc\x99\\\xd1\xca\xc5B\xc9z\xaf{`\xcf=\x9d\x04\x01-I0\xad\xa3#G>O\x0f)\xfd\xc3\x02\x9btA\x06\x93-e\x10\xfbz\xc9\x06\xc7\xd9\xea\xfa\xee\x9dT5\x82\xed\xa8\xb2.\x97\xba\x0e\xf5\xbbu\x97f\xfc\xc0\x01yO2f\xa7;V\x13\x9d\xfb8\xf9v\x8f\x98+\xc6X[\x9c\xba\x8fn\x16om-\xc1\xf3,\xf4\x02@Y\x82\xdc\xae\xac\x19\xe8\xa5\xb6\xdd\x88\x9f\xd25P\xeb\x8a\xbc\xb1\xf6\xba\x11T\xc5\x011\xabB\x94\x10\n\xe7%\xa1\x1b\xc1\n*\xf9[e/O\xaa\x02\xe3\x9a\x7f5\xbe"!\x8c\x94v\x8d,\xf0\x8e\x0ey\x9c8&m\x07\xa6\x13\x04\x97\x1e?\xa7\x9d\xa0\'\xd8\x176\x83\xd

### Looking for missing data

In [ ]:
while True:
    missing_id = [idx for idx,e in enumerate(mylist) if e is None]
    if len(missing_id) == 0:
        logging.info('Got all data')
        data = b'Got all data'
        for n in range(len(data) // PACKETS_SIZE + 1):
            BOB.send(data[n * PACKETS_SIZE: (n + 1) * PACKETS_SIZE])
            BOB.send(SENTINEL)
        break
    else:
        logging.info("Missing data : "+str(missing_id))
        data = pk.dumps(missing_id)
        for n in range(len(data) // PACKETS_SIZE + 1):
            BOB.send(data[n * PACKETS_SIZE: (n + 1) * PACKETS_SIZE])
            BOB.send(SENTINEL)
        while True:
            b_data = b''.join(iter((lambda :BOB.recv(PACKETS_SIZE)), SENTINEL))
            if b_data=b'DONE': break
            data = pk.loads(b_data)
            b_X[data[0]]=data[1]
            b_Y[data[0]]=data[2]